In [1]:
pip install numpy==1.22.4

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.8/16.8 MB 34.6 MB/s eta 0:00:00
  Attempting uninstall: numpy
    Found existing installation: numpy 1.24.3
    Uninstalling numpy-1.24.3:
      Successfully uninstalled numpy-1.24.3
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf 23.8.0 requires cupy-cuda11x>=12.0.0, which is not installed.
cuml 23.8.0 requires cupy-cuda11x>=12.0.0, which is not installed.
dask-cudf 23.8.0 requires cupy-cuda11x>=12.0.0, which is not installed.
apache-beam 2.46.0 requires dill<0.3.2,>=0.3.1.1, but you have dill 0.3.7 which is incompatible.
apache-beam 2.46.0 requires pyarrow<10.0.0,>=3.0.0, but you have pyarrow 11.0.0 which is incompatible.
chex 0.1.84 requires numpy>=1.24.1, but you have numpy 1.22.4 which is incompatible.
cudf 23.8.0 requires pandas<1.6.0dev0,>=1.3, but you have pandas 2.0.3 which is incompatible.
cudf 23.

In [2]:
import numpy as np
import pandas as pd
import plotly.express as px
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)


import statsmodels.api as sm
import tensorflow as tf
from tensorflow import keras

from keras.layers import GRU, Dropout, SimpleRNN, LSTM, Dense
from keras.models import Sequential
from sklearn.preprocessing import MinMaxScaler

/opt/conda/lib/python3.10/site-packages/scipy/__init__.py:146: UserWarning:

A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.24.3



Date: The date on which the particular market data was recorded or reported.

Open: The price at which a particular security (stock, currency, etc.) opened for trading at the beginning of the trading day.

High: The highest price at which the security traded during the trading day.

Low: The lowest price at which the security traded during the trading day.

Close: The price at which the security closed trading at the end of the trading day.

Adj Close (Adjusted Close): The adjusted closing price reflects the security's value at the end of the trading day, adjusted for corporate actions (such as stock splits, dividends, etc.) that occurred after the market's close.

Volume: The total number of shares or contracts traded during a given period. It represents the level of activity or liquidity in the market for that security.

In [3]:
google_stock_train_data = pd.read_csv("/kaggle/input/google-stock-2010-2023/Google_Stock_Train (2010-2022).csv", parse_dates=['Date'])

In [4]:
google_stock_train_data.head()

Date       Open       High        Low      Close  Adj Close     Volume
0 2010-01-04  15.689439  15.753504  15.621622  15.684434  15.684434   78169752
1 2010-01-05  15.695195  15.711712  15.554054  15.615365  15.615365  120067812
2 2010-01-06  15.662162  15.662162  15.174174  15.221722  15.221722  158988852
3 2010-01-07  15.250250  15.265265  14.831081  14.867367  14.867367  256315428
4 2010-01-08  14.814815  15.096346  14.742492  15.065566  15.065566  188783028

In [5]:
google_stock_train_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3272 entries, 0 to 3271
Data columns (total 7 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   Date       3272 non-null   datetime64[ns]
 1   Open       3272 non-null   float64       
 2   High       3272 non-null   float64       
 3   Low        3272 non-null   float64       
 4   Close      3272 non-null   float64       
 5   Adj Close  3272 non-null   float64       
 6   Volume     3272 non-null   int64         
dtypes: datetime64[ns](1), float64(5), int64(1)
memory usage: 179.1 KB


In [6]:
# Lets see the line chart for google stock prices over time
fig1 = px.line(google_stock_train_data, x='Date', y='Close', title='Google Stock Price Over Time')
fig1.show()

/opt/conda/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [7]:
# Lets take a look at daily trading volume
fig2 = px.scatter(google_stock_train_data, x='Date', y='Volume', title='Daily Trading Volume')
fig2.show()

/opt/conda/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [8]:
# Lets get the five number summary for Google stock prices for each year
google_stock_train_data['Year'] = google_stock_train_data['Date'].dt.year
summary_by_year = google_stock_train_data.groupby('Year')['Close'].describe()
summary_by_year

count        mean        std        min         25%         50%  \
Year                                                                    
2010  252.0   13.403981   1.262781  10.912663   12.265453   13.371371   
2011  252.0   14.238593   1.072171  11.883884   13.279279   14.450575   
2012  250.0   16.086498   1.324606  13.990240   15.140328   15.835711   
2013  252.0   22.128197   2.470652  17.589338   20.273836   21.928179   
2014  252.0   28.406118   1.262285  24.908001   27.383375   28.511249   
2015  252.0   30.999411   4.359576  24.853001   27.332625   28.694001   
2016  252.0   38.160661   1.870102  34.056999   36.524375   38.087499   
2017  251.0   46.988653   3.768367  40.388500   42.837502   47.377499   
2018  251.0   56.102179   3.479520  49.233501   53.408501   55.602501   
2019  252.0   59.560847   3.989570  51.273499   56.326999   59.474500   
2020  253.0   73.949656   8.758162  52.706501   69.858498   73.955498   
2021  252.0  124.224887  18.331974  86.143997  110.350372  124.811001   
2022  251.0  114.760371  16.109141  83.430000  100.879998  113.891998   

             75%         max  
Year                          
2010   14.549112   15.684935  
2011   15.245057   16.163664  
2012   17.041041   19.220470  
2013   22.676051   28.045795  
2014   29.468100   30.534784  
2015   34.082375   39.698002  
2016   39.993249   41.786999  
2017   49.627001   54.254501  
2018   58.830999   64.275002  
2019   62.078126   68.123497  
2020   78.229500   91.248497  
2021  141.636498  149.838501  
2022  129.215500  148.000000

In [9]:
# box plot for Google stock prices for each year
fig3 = px.box(google_stock_train_data, x='Year', y='Close', title='Google Stock Prices - Yearly Box Plot')
fig3.show()

In [10]:
fig4 = go.Figure(data=[go.Candlestick(x=np.array(google_stock_train_data['Date']),
                                     open=google_stock_train_data['Open'],
                                     high=google_stock_train_data['High'],
                                     low=google_stock_train_data['Low'],
                                     close=google_stock_train_data['Close'])])

fig4.update_layout(title='Google Stock Prices - Candlestick Chart',
                   xaxis_title='Date',
                   yaxis_title='Stock Price')

fig4.show()


In [11]:
# Histogram of daily returns
google_stock_train_data['Daily_Return'] = google_stock_train_data['Close'].pct_change()
fig5 = px.histogram(google_stock_train_data, x='Daily_Return', nbins=30, title='Distribution of Daily Returns')
fig5.show()

In [12]:
# Heatmap of correlation matrix
correlation_matrix = google_stock_train_data.corr()
fig6 = px.imshow(correlation_matrix, x=correlation_matrix.index, y=correlation_matrix.columns, title='Correlation Matrix Heatmap')
fig6.show()

In [13]:
# Moving average of closing prices
google_stock_train_data['MA_50'] = google_stock_train_data['Close'].rolling(window=50).mean()
fig7 = px.line(google_stock_train_data, x='Date', y=['Close', 'MA_50'], title='Google Stock Price with 50-Day Moving Average')
fig7.show()

/opt/conda/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [14]:
# Scatter plot of closing prices vs. trading volume
fig8 = px.scatter(google_stock_train_data, x='Close', y='Volume', title='Closing Prices vs. Trading Volume')
fig8.show()

In [15]:
# Line chart for daily stock price change
google_stock_train_data['Daily_Change'] = google_stock_train_data['Close'].diff()
fig9 = px.line(google_stock_train_data, x='Date', y='Daily_Change', title='Daily Stock Price Change')
fig9.show()

/opt/conda/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [16]:
# Bar chart of trading volume per month
google_stock_train_data['Month'] = google_stock_train_data['Date'].dt.month
monthly_volume = google_stock_train_data.groupby('Month')['Volume'].sum().reset_index()
fig10 = px.bar(monthly_volume, x='Month', y='Volume', title='Total Trading Volume per Month')
fig10.show()

In [17]:
# Area chart for daily trading volume
fig11 = px.area(google_stock_train_data, x='Date', y='Volume', title='Daily Trading Volume (Area Chart)')
fig11.show()

/opt/conda/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [18]:
# Histogram of daily stock price changes
fig12 = px.histogram(google_stock_train_data, x='Daily_Change', title='Distribution of Daily Stock Price Changes')
fig12.show()

In [19]:
# Line chart for daily stock price percent change
google_stock_train_data['Daily_Pct_Change'] = google_stock_train_data['Close'].pct_change() * 100
fig13 = px.line(google_stock_train_data, x='Date', y='Daily_Pct_Change', title='Daily Stock Price Percent Change')
fig13.show()

/opt/conda/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [20]:
# Box plot of daily stock price percent change by month
fig14 = px.box(google_stock_train_data, x='Month', y='Daily_Pct_Change', title='Daily Stock Price Percent Change by Month')
fig14.show()

In [21]:
# Scatter plot of closing prices with trendline
fig15 = px.scatter(google_stock_train_data, x='Date', y='Close', title='Google Stock Prices with Trendline', trendline='lowess')
fig15.show()

/opt/conda/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result

/opt/conda/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [22]:
# Line chart for daily trading volume with moving average
google_stock_train_data['MA_Volume'] = google_stock_train_data['Volume'].rolling(window=10).mean()
fig16 = px.line(google_stock_train_data, x='Date', y=['Volume', 'MA_Volume'], title='Daily Trading Volume with 10-Day Moving Average')
fig16.show()

/opt/conda/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [23]:
# Box plot of daily stock price changes by year
fig17 = px.box(google_stock_train_data, x='Year', y='Daily_Change', title='Daily Stock Price Changes by Year')
fig17.show()

In [24]:
# Line chart for daily closing prices in 2022
df_2022 = google_stock_train_data[google_stock_train_data['Year'] == 2022]
fig18 = px.line(google_stock_train_data, x='Date', y='Close', title='Google Stock Prices in 2022')
fig18.show()

/opt/conda/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [25]:
# Scatter plot of daily returns vs. trading volume
fig19 = px.scatter(google_stock_train_data, x='Daily_Return', y='Volume', title='Daily Returns vs. Trading Volume')
fig19.show()

In [26]:
# Line chart for daily trading volume with range slider
fig20 = px.line(google_stock_train_data, x='Date', y='Volume', title='Daily Trading Volume with Range Slider')
fig20.update_xaxes(rangeslider_visible=True)
fig20.show()

/opt/conda/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [27]:
google_stock_train_data.columns

Index(['Date', 'Open', 'High', 'Low', 'Close', 'Adj Close', 'Volume', 'Year',
       'Daily_Return', 'MA_50', 'Daily_Change', 'Month', 'Daily_Pct_Change',
       'MA_Volume'],
      dtype='object')

In [28]:
google_training_processed = google_stock_train_data['Adj Close'].values.reshape(-1, 1)
google_training_processed

array([[15.684434],
       [15.615365],
       [15.221722],
       ...,
       [86.019997],
       [88.449997],
       [88.230003]])

In [29]:
scaler = MinMaxScaler(feature_range = (0, 1))
scaled_data = scaler.fit_transform(google_training_processed)
scaled_data, scaled_data.shape

(array([[0.03434761],
        [0.03385045],
        [0.03101697],
        ...,
        [0.54062898],
        [0.55812033],
        [0.55653679]]),
 (3272, 1))

In [30]:
# lets create feature set to predict next day market based on past 60 days data
features_set = []
labels = []
for i in range(60, scaled_data.shape[0]):
    features_set.append(scaled_data[i-60:i, 0])
    labels.append(scaled_data[i, 0])

In [31]:
features_set, labels = np.array(features_set), np.array(labels)

In [32]:
features_set.shape, labels.shape

((3212, 60), (3212,))

In [33]:
features_set = np.reshape(features_set, (features_set.shape[0], features_set.shape[1], 1))
features_set.shape


(3212, 60, 1)

In [34]:
np.array(features_set)

array([[[0.03434761],
        [0.03385045],
        [0.03101697],
        ...,
        [0.02280834],
        [0.02276511],
        [0.02353248]],

       [[0.03385045],
        [0.03101697],
        [0.0284663 ],
        ...,
        [0.02276511],
        [0.02353248],
        [0.02360633]],

       [[0.03101697],
        [0.0284663 ],
        [0.02989295],
        ...,
        [0.02353248],
        [0.02360633],
        [0.02390895]],

       ...,

       [[0.63146883],
        [0.65306308],
        [0.65155149],
        ...,
        [0.55315368],
        [0.56373488],
        [0.55049037]],

       [[0.65306308],
        [0.65155149],
        [0.6514795 ],
        ...,
        [0.56373488],
        [0.55049037],
        [0.54062898]],

       [[0.65155149],
        [0.6514795 ],
        [0.63175676],
        ...,
        [0.55049037],
        [0.54062898],
        [0.55812033]]])

# RNN

In [35]:
RNN_model = Sequential()
RNN_model.add(SimpleRNN(units = 300, return_sequences = True, input_shape=(features_set.shape[1], 1)))
RNN_model.add(Dropout(0.2))

RNN_model.add(SimpleRNN(units = 100, return_sequences = True, input_shape=(features_set.shape[1], 1)))
RNN_model.add(Dropout(0.2))

RNN_model.add(SimpleRNN(units = 100, return_sequences = True))
RNN_model.add(Dropout(0.2))

RNN_model.add(SimpleRNN(units = 100))
RNN_model.add(Dropout(0.2))

RNN_model.add(Dense(units = 1))

In [36]:
#Compile the model
RNN_model.compile(optimizer = 'adam', loss='mean_squared_error')

In [37]:
RNN_model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 simple_rnn (SimpleRNN)      (None, 60, 300)           90600     
                                                                 
 dropout (Dropout)           (None, 60, 300)           0         
                                                                 
 simple_rnn_1 (SimpleRNN)    (None, 60, 100)           40100     
                                                                 
 dropout_1 (Dropout)         (None, 60, 100)           0         
                                                                 
 simple_rnn_2 (SimpleRNN)    (None, 60, 100)           20100     
                                                                 
 dropout_2 (Dropout)         (None, 60, 100)           0         
                                                                 
 simple_rnn_3 (SimpleRNN)    (None, 100)               2

In [38]:
RNN_history = RNN_model.fit(features_set, labels, epochs=300, batch_size=32)

Epoch 1/300
101/101 [==============================] - 27s 183ms/step - loss: 0.5933
Epoch 2/300
101/101 [==============================] - 19s 188ms/step - loss: 0.2621
Epoch 3/300
101/101 [==============================] - 19s 184ms/step - loss: 0.2007
Epoch 4/300
101/101 [==============================] - 18s 183ms/step - loss: 0.1424
Epoch 5/300
101/101 [==============================] - 18s 183ms/step - loss: 0.1007
Epoch 6/300
101/101 [==============================] - 18s 183ms/step - loss: 0.0911
Epoch 7/300
101/101 [==============================] - 18s 182ms/step - loss: 0.0629
Epoch 8/300
101/101 [==============================] - 18s 181ms/step - loss: 0.0615
Epoch 9/300
101/101 [==============================] - 19s 184ms/step - loss: 0.0416
Epoch 10/300
101/101 [==============================] - 19s 184ms/step - loss: 0.0342
Epoch 11/300
101/101 [==============================] - 18s 182ms/step - loss: 0.0256
Epoch 12/300
101/101 [==============================] - 19s 185

# LSTM

In [39]:
LSTM_model = Sequential()
LSTM_model.add(LSTM(units = 300, return_sequences=True, input_shape=(features_set.shape[1], 1)))
LSTM_model.add(Dropout(0.2))

LSTM_model.add(LSTM(units = 100, return_sequences=True))
LSTM_model.add(Dropout(0.2))

LSTM_model.add(LSTM(units = 100, return_sequences=True))
LSTM_model.add(Dropout(0.2))

LSTM_model.add(LSTM(units = 100))
LSTM_model.add(Dropout(0.2))
               
LSTM_model.add(Dense(units=1))

In [40]:
LSTM_model.compile(optimizer='adam', loss='mean_squared_error')

In [41]:
LSTM_model.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm (LSTM)                 (None, 60, 300)           362400    
                                                                 
 dropout_4 (Dropout)         (None, 60, 300)           0         
                                                                 
 lstm_1 (LSTM)               (None, 60, 100)           160400    
                                                                 
 dropout_5 (Dropout)         (None, 60, 100)           0         
                                                                 
 lstm_2 (LSTM)               (None, 60, 100)           80400     
                                                                 
 dropout_6 (Dropout)         (None, 60, 100)           0         
                                                                 
 lstm_3 (LSTM)               (None, 100)              

In [42]:
LSTM_history = LSTM_model.fit(features_set, labels, epochs = 300, batch_size=32)

Epoch 1/300
101/101 [==============================] - 9s 14ms/step - loss: 0.0064
Epoch 2/300
101/101 [==============================] - 1s 12ms/step - loss: 0.0014
Epoch 3/300
101/101 [==============================] - 1s 13ms/step - loss: 0.0021
Epoch 4/300
101/101 [==============================] - 1s 13ms/step - loss: 0.0012
Epoch 5/300
101/101 [==============================] - 1s 13ms/step - loss: 0.0013
Epoch 6/300
101/101 [==============================] - 1s 12ms/step - loss: 0.0012
Epoch 7/300
101/101 [==============================] - 1s 12ms/step - loss: 0.0013
Epoch 8/300
101/101 [==============================] - 1s 12ms/step - loss: 9.6031e-04
Epoch 9/300
101/101 [==============================] - 1s 13ms/step - loss: 0.0010
Epoch 10/300
101/101 [==============================] - 1s 12ms/step - loss: 8.8228e-04
Epoch 11/300
101/101 [==============================] - 1s 13ms/step - loss: 8.8726e-04
Epoch 12/300
101/101 [==============================] - 1s 13ms/step - lo

# GRU

In [43]:
GRU_model = Sequential()
GRU_model.add(GRU(units=300, return_sequences=True, input_shape=(features_set.shape[1], 1)))
GRU_model.add(Dropout(0.2))

GRU_model.add(GRU(units=100, return_sequences=True))
GRU_model.add(Dropout(0.2))

GRU_model.add(GRU(units=100, return_sequences=True))
GRU_model.add(Dropout(0.2))

GRU_model.add(GRU(units=100))
GRU_model.add(Dropout(0.2))

GRU_model.add(Dense(units=1))


In [44]:
GRU_model.compile(optimizer = 'adam', loss='mean_squared_error')

In [45]:
GRU_model.summary()

Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 gru (GRU)                   (None, 60, 300)           272700    
                                                                 
 dropout_8 (Dropout)         (None, 60, 300)           0         
                                                                 
 gru_1 (GRU)                 (None, 60, 100)           120600    
                                                                 
 dropout_9 (Dropout)         (None, 60, 100)           0         
                                                                 
 gru_2 (GRU)                 (None, 60, 100)           60600     
                                                                 
 dropout_10 (Dropout)        (None, 60, 100)           0         
                                                                 
 gru_3 (GRU)                 (None, 100)              

In [46]:
GRU_history = GRU_model.fit(features_set, labels, epochs=300, batch_size=32)

Epoch 1/300
101/101 [==============================] - 8s 14ms/step - loss: 0.0066
Epoch 2/300
101/101 [==============================] - 1s 12ms/step - loss: 0.0012
Epoch 3/300
101/101 [==============================] - 1s 12ms/step - loss: 0.0013
Epoch 4/300
101/101 [==============================] - 1s 12ms/step - loss: 0.0010
Epoch 5/300
101/101 [==============================] - 1s 12ms/step - loss: 0.0013
Epoch 6/300
101/101 [==============================] - 1s 12ms/step - loss: 0.0011
Epoch 7/300
101/101 [==============================] - 1s 12ms/step - loss: 7.7471e-04
Epoch 8/300
101/101 [==============================] - 1s 12ms/step - loss: 0.0010
Epoch 9/300
101/101 [==============================] - 1s 12ms/step - loss: 7.6026e-04
Epoch 10/300
101/101 [==============================] - 1s 12ms/step - loss: 9.6881e-04
Epoch 11/300
101/101 [==============================] - 1s 12ms/step - loss: 8.1172e-04
Epoch 12/300
101/101 [==============================] - 1s 12ms/step 

# Model Evaluation

In [47]:
fig = go.Figure()

#Training Loss Trace
fig.add_trace(go.Scatter(x=list(range(1, len(RNN_history.history['loss'])+1)), 
                        y=RNN_history.history['loss'],
                        mode='lines',
                        name='RNN Training Loss'))

fig.add_trace(go.Scatter(x=list(range(1, len(LSTM_history.history['loss'])+1)), 
                        y=LSTM_history.history['loss'],
                        mode='lines',
                        name='LSTM Training Loss'))

fig.add_trace(go.Scatter(x=list(range(1, len(GRU_history.history['loss'])+1)), 
                        y=GRU_history.history['loss'],
                        mode='lines',
                        name='GRU Training Loss'))

fig.update_layout(title='Training and Validation Loss',
                 xaxis_title = 'Epoch',
                 yaxis_title = 'Loss',
                 legend_title = 'Loss Type',
                 hovermode='x',
                 hoverlabel=dict(bgcolor='white', font_size=12, font_family='Rockwell'), template='plotly_white')

fig.show()

# Evaluate Model Prediction

In [48]:
google_testing_complete = pd.read_csv("/kaggle/input/google-stock-2010-2023/Google_Stock_Test (2023).csv")
google_testing_processed = google_testing_complete.iloc[:, 1:2].values

google_total = pd.concat((google_stock_train_data['Close'], google_testing_complete['Close']), axis=0)

test_inputs = google_total[len(google_total) - len(google_testing_complete) - 60:].values
test_inputs


array([101.419998,  98.68    ,  97.860001,  97.18    ,  97.559998,
        99.059998,  96.559998,  99.970001, 100.769997,  99.629997,
        99.970001, 101.129997, 102.519997, 104.480003,  94.93    ,
        92.220001,  96.290001,  94.510002,  90.470001,  86.970001,
        83.43    ,  86.580002,  88.489998,  88.900002,  87.32    ,
        93.940002,  96.410004,  95.699997,  98.440002,  98.849998,
        98.360001,  97.43    ,  95.599998,  97.050003,  98.459999,
        97.459999,  96.050003,  95.190002, 100.989998, 100.989998,
       100.440002,  99.480003,  96.980003,  94.940002,  93.709999,
        92.830002,  93.309998,  95.629997,  95.07    ,  90.860001,
        90.260002,  88.440002,  89.019997,  89.580002,  87.760002,
        89.230003,  87.389999,  86.019997,  88.449997,  88.230003,
        89.120003,  88.080002,  86.199997,  87.339996,  88.019997,
        88.419998,  91.519997,  91.129997,  92.120003,  91.290001,
        91.120003,  93.050003,  98.019997,  99.790001,  97.699

In [49]:
test_inputs = test_inputs.reshape(-1,1)
test_inputs = scaler.transform(test_inputs)

test_features = []
for i in range(60, len(test_inputs)):
    test_features.append(test_inputs[i-60:i, 0])
    
test_features = np.array(test_features)
test_features = np.reshape(test_features, (test_features.shape[0], test_features.shape[1], 1))
test_features.shape

(143, 60, 1)

In [50]:
# Evaluate the model on the test set
## RNN
RNN_test_loss = RNN_model.evaluate(test_features, google_testing_processed)
print(f'RNN Test Loss: {RNN_test_loss}')

## LSTM
LSTM_test_loss = LSTM_model.evaluate(test_features, google_testing_processed)
print(f'LSTM Test Loss: {LSTM_test_loss}')

## GRU
GRU_test_loss = GRU_model.evaluate(test_features, google_testing_processed)
print(f'LSTM Test Loss: {GRU_test_loss}')

5/5 [==============================] - 1s 20ms/step - loss: 11656.8213
RNN Test Loss: 11656.8212890625
5/5 [==============================] - 1s 11ms/step - loss: 11554.5283
LSTM Test Loss: 11554.5283203125
5/5 [==============================] - 1s 11ms/step - loss: 11558.8584
LSTM Test Loss: 11558.8583984375


# Making Predictions

In [51]:
# RNN
RNN_predictions = RNN_model.predict(test_features)
RNN_predictions = scaler.inverse_transform(RNN_predictions)

# LSTM
LSTM_predictions = LSTM_model.predict(test_features)
LSTM_predictions = scaler.inverse_transform(LSTM_predictions)

# GRU
GRU_predictions = GRU_model.predict(test_features)
GRU_predictions = scaler.inverse_transform(GRU_predictions)

5/5 [==============================] - 1s 8ms/step


In [52]:
google_testing_complete

Date        Open        High         Low       Close   Adj Close  \
0    2023-01-03   89.589996   91.050003   88.519997   89.120003   89.120003   
1    2023-01-04   90.349998   90.650002   87.269997   88.080002   88.080002   
2    2023-01-05   87.470001   87.570000   85.900002   86.199997   86.199997   
3    2023-01-06   86.790001   87.690002   84.860001   87.339996   87.339996   
4    2023-01-09   88.360001   90.050003   87.860001   88.019997   88.019997   
..          ...         ...         ...         ...         ...         ...   
138  2023-07-24  121.660004  123.000000  120.980003  121.529999  121.529999   
139  2023-07-25  121.360001  123.150002  121.019997  122.209999  122.209999   
140  2023-07-26  130.070007  130.979996  128.320007  129.270004  129.270004   
141  2023-07-27  131.669998  133.240005  128.789993  129.399994  129.399994   
142  2023-07-28  130.779999  133.740005  130.570007  132.580002  132.580002   

       Volume  
0    28131200  
1    34854800  
2    27194400  
3    41381500  
4    29003900  
..        ...  
138  29686100  
139  52509600  
140  61682100  
141  44952100  
142  36572900  

[143 rows x 7 columns]

In [53]:
google_prediction = google_testing_complete['Date']
google_prediction = pd.DataFrame(google_prediction)
google_prediction['RNN_Open'] = RNN_predictions
google_prediction['LSTM_Open'] = LSTM_predictions
google_prediction['GRU_Open'] = GRU_predictions

google_prediction

Date   RNN_Open   LSTM_Open    GRU_Open
0    2023-01-03  44.160282   89.391212   88.370918
1    2023-01-04  44.160282   90.188843   88.786926
2    2023-01-05  44.160282   89.317268   88.809891
3    2023-01-06  44.160282   87.209457   88.119339
4    2023-01-09  44.160282   87.717087   87.922905
..          ...        ...         ...         ...
138  2023-07-24  44.160282  122.156021  120.103355
139  2023-07-25  44.160282  123.535568  120.259315
140  2023-07-26  44.160286  124.231789  120.774239
141  2023-07-27  44.160282  130.401718  123.727852
142  2023-07-28  44.160282  131.354767  125.952789

[143 rows x 4 columns]

In [54]:
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)

In [55]:
fig = go.Figure()

# Actual google stock price trace
fig.add_trace(go.Scatter(x=google_testing_complete.Date,
                         y=google_testing_complete.Open,
                         mode='lines',
                         name='Actual Google Stock Price',
                         line=dict(color='blue')))

# RNN Predicted google stock price trace
fig.add_trace(go.Scatter(x=google_prediction.Date,
                         y=google_prediction.RNN_Open,
                         mode='lines',
                         name='RNN Predicted Google Stock Price',
                         line=dict(color='red')))

# LSTM Predicted google stock price trace
fig.add_trace(go.Scatter(x=google_prediction.Date,
                         y=google_prediction.LSTM_Open,
                         mode='lines',
                         name='LSTM Predicted Google Stock Price',
                         line=dict(color='green')))
# LSTM Predicted google stock price trace
fig.add_trace(go.Scatter(x=google_prediction.Date,
                         y=google_prediction.GRU_Open,
                         mode='lines',
                         name='GRU Predicted Google Stock Price',
                         line=dict(color='yellow')))

fig.update_layout(title='Google Stock Price Prediction',
                  xaxis_title='Date',
                  yaxis_title='Google Stock Price',
                  legend_title='Price Type',
                  hovermode='x',
                  hoverlabel=dict(bgcolor='white', font_size=12, font_family='Rockwell'),
                  template='plotly_white')

fig.show()